In [1]:
import numpy as np
import cv2
import matplotlib.pyplot as plt
from tqdm import tqdm
from skimage.segmentation import slic, mark_boundaries
import os
from npGraph import Graph, visuals
import torch

ModuleNotFoundError: No module named 'torch'

In [2]:
im = cv2.imread("raw_data/images/0939.control.40.a.tif", 0)

In [13]:
bilat_im = cv2.bilateralFilter(im, d=10, sigmaColor=80, sigmaSpace=80)
segments = slic(im, n_segments=400, compactness=0.1, start_label=0)
fig, axs = plt.subplots(2, 2, figsize=(30,30))
axs[0, 0].imshow(im)
axs[0, 1].imshow(bilat_im)
axs[1, 0].imshow(mark_boundaries(im, segments))
axs[1, 1].imshow(mark_boundaries(np.zeros_like(im), segments))

In [4]:
def im2graph(im, n_segments=10000, compactness=0.1):
    segments = slic(im, n_segments=n_segments, compactness=compactness, start_label=0)
    num_nodes = np.unique(segments).shape[0]
    graph = np.zeros((num_nodes, num_nodes))
    sp_means = {i:np.mean(im[np.where(segments==i)]) for i in np.unique(segments)}
    for x in range(im.shape[0]-1):
        for y in range(im.shape[1]-1):
            if segments[x, y] != segments[x+1, y]:
                edge_weight = (sp_means[segments[x, y]]-sp_means[segments[x+1, y]])**2
                graph[segments[x, y],segments[x+1, y]] = 1-edge_weight
                graph[segments[x+1, y],segments[x, y]] = 1-edge_weight
            if segments[x, y] != segments[x, y+1]:
                edge_weight = (sp_means[segments[x, y]]-sp_means[segments[x, y+1]])**2
                graph[segments[x, y],segments[x, y+1]] = 1-edge_weight
                graph[segments[x, y+1],segments[x, y]] = 1-edge_weight
    return graph

In [5]:
G = Graph.from_adj(im2graph(im))

In [6]:
G.adj[G.adj<0.8]=0

In [7]:
G.adj[G.adj>0].shape

(43616,)

In [16]:
groups = [set(list(np.where(i>0)[0])+[n]) for n,i in enumerate(G.adj)]

In [9]:
merged_groups = []
for i in tqdm(range(len(groups))):
    x = groups[i]
    for j in range(len(groups)):
        if x.intersection(groups[j]):
            x = x.union(groups[j])
    if x not in merged_groups:
        merged_groups.append(x)

100%|██████████| 7821/7821 [07:37<00:00, 17.09it/s] 


In [67]:
merged_groups = []
completed_nodes = set()
for i in tqdm(groups):
    if len(completed_nodes)==len(groups):
        break
    x = i.copy()
    for j in groups:
        if x.intersection(j):
                x = x.union(j)
                completed_nodes.update(j)
    if not x in merged_groups:
        print(x)
        merged_groups.append(x)

  0%|          | 2/7821 [00:00<23:53,  5.45it/s]

{0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 220, 221,

  0%|          | 9/7821 [00:01<24:13,  5.37it/s]

{0, 1, 2, 3, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 220, 221, 22

  0%|          | 12/7821 [00:02<23:38,  5.50it/s]

...

{101, 102, 103, 104, 105, 106, 107, 108, 109, 118, 121, 124, 126, 140, 141, 161, 213, 215, 219, 239, 253, 254, 265, 266, 299, 300, 318, 320, 321, 323, 326, 337, 338, 345, 346, 351, 352, 355, 364, 365, 366, 407, 412, 416, 420, 426, 434, 442, 443, 448, 465, 466, 467, 468, 469, 470, 491, 492, 493, 499, 500, 501, 507, 508, 516, 517, 518, 527, 541, 542, 547, 548, 555, 563, 564, 587, 588, 589, 590, 591, 592, 593, 599, 600, 601, 609, 610, 619, 624, 630, 653, 654, 655, 663, 664, 665, 666, 670, 671, 674, 675, 697, 698, 699, 700, 701, 706, 707, 708, 716, 721, 722, 733, 738, 746, 747, 755, 764, 765, 766, 767, 768, 781, 782, 783, 800, 801, 802, 803, 804, 808, 811, 814, 818, 823, 824, 828, 841, 848, 849, 850, 866, 867, 868, 869, 870, 871, 880, 881, 889, 890, 891, 907, 908, 909, 910, 911, 912, 913, 916, 923, 940, 944, 945, 946, 953, 954, 955, 956, 957, 978, 984, 985, 997, 998, 999, 1000, 1001, 1002, 1007, 1008, 1015, 1016, 1017, 1018, 1021, 1025, 1040, 1046, 1047, 1054, 1061, 1068, 1069, 1082, 1092,

  2%|▏         | 126/7821 [00:21<20:14,  6.33it/s]

{101, 102, 103, 105, 106, 107, 108, 109, 118, 121, 124, 126, 140, 141, 161, 213, 215, 219, 239, 253, 254, 265, 266, 299, 300, 318, 320, 321, 323, 326, 337, 338, 345, 346, 351, 352, 355, 364, 365, 366, 407, 412, 416, 420, 426, 434, 442, 443, 448, 465, 466, 467, 468, 469, 470, 491, 492, 493, 499, 500, 501, 507, 508, 516, 517, 518, 527, 541, 542, 547, 548, 555, 563, 564, 587, 588, 589, 590, 591, 592, 593, 599, 600, 601, 609, 610, 619, 624, 630, 653, 654, 655, 663, 664, 665, 666, 670, 671, 674, 675, 697, 698, 699, 700, 701, 706, 707, 708, 716, 721, 722, 733, 738, 746, 747, 755, 764, 765, 766, 767, 768, 781, 782, 783, 800, 801, 802, 803, 804, 808, 811, 814, 818, 823, 824, 828, 841, 848, 849, 850, 866, 867, 868, 869, 870, 871, 880, 881, 889, 890, 891, 907, 908, 909, 910, 911, 912, 913, 916, 923, 940, 944, 945, 946, 953, 954, 955, 956, 957, 978, 984, 985, 997, 998, 999, 1000, 1001, 1002, 1007, 1008, 1015, 1016, 1017, 1018, 1021, 1025, 1040, 1046, 1047, 1054, 1061, 1068, 1069, 1082, 1092, 1093

  3%|▎         | 268/7821 [00:44<21:04,  5.97it/s]


KeyboardInterrupt: 

In [62]:
merged_groups

[]